In [9]:
!pip install -q transformers
!pip install -q torch
!pip install -q shap

# Pre-Trained GELECTRA Model

In [15]:
from transformers import pipeline
from transformers import AutoTokenizer, AutoModelForQuestionAnswering

In [16]:
tokenizer = AutoTokenizer.from_pretrained("deepset/gelectra-base-germanquad")
model = AutoModelForQuestionAnswering.from_pretrained("deepset/gelectra-base-germanquad")

nlp_pipelin = pipeline('question-answering', model=model, tokenizer=tokenizer)

In [17]:
test_context = "Aufzugsanlage\n\n=== Seilloser Aufzug ===\nAn der RWTH Aachen im Institut für Elektrische Maschinen wurde ein seilloser Aufzug entwickelt und ein Prototyp aufgebaut. Die Kabine wird hierbei durch zwei elektromagnetische Synchron-Linearmotoren angetrieben und somit nur durch ein vertikal bewegliches Magnetfeld gehalten bzw. bewegt. Diese Arbeit soll der Entwicklung von Aufzugsanlagen für sehr hohe Gebäude dienen. Ein Ziel ist der Einsatz mehrerer Kabinen pro Schacht, die sich unabhängig voneinander steuern lassen. Bei Auswahl des Fahrtziels vor Fahrtantritt (d. h. noch außerhalb des Aufzug) wird ein bestimmter Fahrkorb in einem der Aufzugsschächte für die Fahrt ausgewählt, mit der sich der geplante Transport am schnellsten durchführen lässt. Der Platzbedarf für die gesamte Aufzugsanlage könnte somit um ein oder mehrere Schächte reduziert werden. Da die Kabinen seillos betrieben werden, ist ein Schachtwechsel ebenfalls denkbar. Hiermit können weitere Betriebsstrategien für die seillose Aufzugsanlage entwickelt werden, zum Beispiel ein moderner Paternosteraufzug mit unabhängig voneinander beweglichen Kabinen.\nIm Rahmen der Forschungen an dem seillosen Aufzug wird ebenfalls an der Entwicklung elektromagnetischer Linearführungen gearbeitet, um den Verschleiß der seillosen Aufzugsanlage bei hohem Fahrkomfort zu minimieren. Weltweit wird an verschiedenen Forschungseinrichtungen an seillosen Antriebslösungen für Aufzüge gearbeitet. Otis betreibt zu diesem Zweck seit 2007 den ''Shibayama Test Tower''. ThyssenKrupp Elevator weihte 2017 im süddeutschen Rottweil einen Testturm ein, in welchem die Technik des seillosen Aufzugs mit Synchron-Linearmotoren im Originalmaßstab getestet wird. Der erste Aufzug dieses Typs soll 2020 in Berlin in Betrieb gehen."
test_question = "Was kann den Verschleiß des seillosen Aufzuges minimieren?"

In [18]:
nlp_pipelin({
    'question': test_question,
    'context': test_context
})

{'score': 0.37087827920913696,
 'start': 1193,
 'end': 1240,
 'answer': 'Entwicklung elektromagnetischer Linearführungen'}

# SHAP

In [6]:
import transformers
import shap
import torch

# load the model
pmodel = model

# define two predictions, one that outputs the logits for the range start,
# and the other for the range end
def f(questions, start):
    outs = []
    for q in questions:
        question, context = q.split("[SEP]")
        d = tokenizer(question, context)
        out = model.forward(**{k: torch.tensor(d[k]).reshape(1, -1) for k in d})
        logits = out.start_logits if start else out.end_logits
        outs.append(logits.reshape(-1).detach().numpy())
    return outs
def f_start(questions):
    return f(questions, True)
def f_end(questions):
    return f(questions, False)

# attach a dynamic output_names property to the models so we can plot the tokens at each output position
def out_names(inputs):
    question, context = inputs.split("[SEP]")
    d = tokenizer(question, context)
    return [tokenizer.decode([id]) for id in d["input_ids"]]
f_start.output_names = out_names
f_end.output_names = out_names

In [7]:
data = [test_question + "[SEP]" + test_context]

explainer_start = shap.Explainer(f_start, tokenizer)
shap_values_start = explainer_start(data)

shap.plots.text(shap_values_start)

  0%|          | 0/498 [00:00<?, ?it/s]

Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.

Compilation is falling back to object mode WITH looplifting enabled because Function "_build_fixed_single_output" failed type inference due to: non-precise type array(pyobject, 1d, C)
During: typing of argument at /opt/conda/envs/rapids/lib/python3.7/site-packages/shap/utils/_masked_model.py (366)

File "../../../../../opt/conda/envs/rapids/lib/python3.7/site-packages/shap/utils/_masked_model.py", line 366:
def _build_fixed_single_output(averaged_outs, last_outs, outputs, batch_positions, varying_rows, num_varying_rows, link, linearizing_weights):
    <source elided>
    # to carry over evaluation outputs
    sample_count = last_outs.shape[0]
    ^


Compilation is falling back to object mode WITHOUT looplifting enabled because Function "_build_fixed

ValueError: setting an array element with a sequence.

In [8]:
# load the model
pmodel = transformers.pipeline('question-answering')

# define two predictions, one that outputs the logits for the range start,
# and the other for the range end
def f(questions, start):
    outs = []
    for q in questions:
        question, context = q.split("[SEP]")
        d = pmodel.tokenizer(question, context)
        out = pmodel.model.forward(**{k: torch.tensor(d[k]).reshape(1, -1) for k in d})
        logits = out.start_logits if start else out.end_logits
        outs.append(logits.reshape(-1).detach().numpy())
    return outs
def f_start(questions):
    return f(questions, True)
def f_end(questions):
    return f(questions, False)

# attach a dynamic output_names property to the models so we can plot the tokens at each output position
def out_names(inputs):
    question, context = inputs.split("[SEP]")
    d = pmodel.tokenizer(question, context)
    return [pmodel.tokenizer.decode([id]) for id in d["input_ids"]]
f_start.output_names = out_names
f_end.output_names = out_names

data = ["What is on the table?[SEP]When I got home today I saw my cat on the table, and my frog on the floor."]

explainer_start = shap.Explainer(f_start, pmodel.tokenizer)
shap_values_start = explainer_start(data)

shap.plots.text(shap_values_start)

No model was supplied, defaulted to distilbert-base-cased-distilled-squad and revision 626af31 (https://huggingface.co/distilbert-base-cased-distilled-squad).
Using a pipeline without specifying a model name and revision in production is not recommended.


Downloading:   0%|          | 0.00/473 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/261M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/29.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/213k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/436k [00:00<?, ?B/s]

  0%|          | 0/498 [00:00<?, ?it/s]


Partition explainer: 2it [06:51, 411.24s/it]              
